In [1]:
import os
from functools import partial
from multiprocessing import Pool

import numpy as np
import pandas as pd
import plotly.express as ex
import plotly.graph_objects as go
from hvwfg import wfg
from numba import njit
from pymoo.indicators.spacing import SpacingIndicator
from scipy.spatial import ConvexHull
from scipy.spatial.distance import cdist
from tqdm.notebook import tqdm

from ipa.domination import non_dominated
from ipa.GenerateReferencePoints import generate_points, rotate_in, rotate_out
from ipa.scalarization import ReferencePointASF
from ipa.selection import DSS_numba, DSS_scipy, DSS_scipy_one_liner, angle_distance, random_selection
from ipa.visibility import visibility

In [2]:
parallel_processes = len(os.sched_getaffinity(0))
print(f"Number of parallel processes: {parallel_processes}")

Number of parallel processes: 32


In [3]:
def run_one_exp(
    selection_method,
    asf_solver,
    reference_points,
    bad_reference_check,
    max_iterations=200,
    thickness=0.01,
):
    results = visibility(
        selection_method,
        asf_solver,
        reference_points,
        max_iterations,
        bad_reference_check,
        thickness=thickness,
    )

    return results


def get_forest_problem(n_objs=3):
    dataT = pd.read_csv("../data/forest.csv")
    # Calculate correlation between columns of data

    # Objs chosen based on correlation matrix

    if n_objs == 3:
        dataT = dataT[["Rev", "HA", "Carb"]]
    elif n_objs != 4:
        raise ValueError("Number of objectives must be 3 or 4")

    dataT = dataT[non_dominated(-dataT.to_numpy())]

    # Convert to minimization problem, and normalize
    data = -dataT
    data = (data - data.min()) / (data.max() - data.min())

    ideal = np.zeros(n_objs)
    nadir = np.ones(n_objs)

    data_np = data.to_numpy()
    return data_np, ideal, nadir, n_objs


def get_dtlz(filename):
    dataT = pd.read_csv(f"../data/{filename}.csv")

    dataT = dataT[non_dominated(-dataT.to_numpy())]

    # Convert to minimization problem, and normalize
    data = dataT
    data = (data - data.min()) / (data.max() - data.min())

    ideal = np.array([0] * data.shape[1])
    nadir = np.array([1] * data.shape[1])

    data_np = data.to_numpy()
    return data_np, ideal, nadir, data.shape[1]


def get_re(filename):
    dataT = pd.read_csv(f"../data/{filename}.csv")

    dataT = dataT[non_dominated(dataT.to_numpy())]

    # Convert to minimization problem, and normalize
    data = dataT
    data = (data - data.min()) / (data.max() - data.min())

    ideal = np.array([0] * data.shape[1])
    nadir = np.array([1] * data.shape[1])

    data_np = data.to_numpy()
    return data_np, ideal, nadir, data.shape[1]


from time import process_time

from pydantic import BaseModel, Field


class OneExperimentResults(BaseModel):
    problemName: str = Field(description="Name of the problem")
    method: str = Field(description="Name of the method")
    runID: int = Field(description="Run number")
    hv: list[float] = Field(description="Hypervolume (Normalized) of the found solutions at each iteration")
    IDG: list[float] = Field("IGD of the found solutions at each iteration")
    RSE: list[float] = Field("Log RSE of the found solutions at each iteration")
    spacing: list[float] = Field("Spacing indicator value of the found solutions at each iteration")
    CumBadRefs: list[float] = Field(description="Cumulative fraction of bad reference points found at each iteration")
    success: list[bool] = Field(description="Whether the method evaluated a valid reference point at each iteration")
    runtime: float = Field(description="Runtime of the experiment")
    found_solutions: list[list[float]] = Field(description="Found solutions at each iteration")
    evaluated_refs: list[list[float]] = Field(description="Evaluated reference points at each iteration")


class ExperimentResults(BaseModel):
    results: list[OneExperimentResults] = Field(description="Results of the experiment")


def exp_results(
    results,
    data,
    name,
    method,
    runID,
    runtime,
    spacing_ind,
):
    hv = []
    found_sols = np.array([result["solution"] for result in results])
    evaluated_refs = np.array([result["ref_point"] for result in results])
    num_dims = len(found_sols[0])
    nadir = np.ones(num_dims) * 1.1
    for i in range(len(found_sols)):
        hv.append(wfg(found_sols[: i + 1], nadir.astype(float)))

    hv = np.array(hv) / wfg(np.ascontiguousarray(data), nadir.astype(float))
    cum_bad = [result["bad_fraction"] for result in results]

    igd = [IGD(data, found_sols[: i + 1]) for i in range(len(found_sols))]
    # spacing_ind = SpacingIndicator(pf=data, zero_to_one=True)
    spacing_ind_value = [np.nan] * 5 + [spacing_ind(found_sols[: i + 1]) for i in range(5, len(found_sols))]
    rse = [np.nan] * 5 + [RSE(found_sols[: i + 1]) for i in range(5, len(found_sols))]

    return OneExperimentResults(
        problemName=name,
        method=method,
        runID=runID,
        hv=hv.tolist(),
        IDG=igd,
        RSE=rse,
        spacing=spacing_ind_value,
        success=[result["success"] for result in results],
        CumBadRefs=cum_bad,
        runtime=runtime,
        found_solutions=found_sols.tolist(),
        evaluated_refs=evaluated_refs.tolist(),
    )


def IGD(data, approx):
    """
    Calculate the IGD of a set of approximations
    """
    return np.mean(np.min(cdist(data, approx), axis=1))


@njit()
def RSEnumba(distances, power):
    """
    Calculate the ln(RSE) of a set of approximations based on the pairwise distances
    """
    rse = 0
    for i in range(len(distances)):
        for j in range(i + 1, len(distances)):
            rse += distances[i, j] ** power
    return np.log(rse)


def RSE(approx):
    """
    Calculate the RSE of a set of approximations
    """
    distances = cdist(approx, approx)
    num_objs = approx.shape[1]
    return RSEnumba(distances, num_objs - 1)

In [4]:
def total_random(
    available: np.ndarray,
    taken: np.ndarray,
    reference_points: np.ndarray,
) -> int:
    return np.random.choice(range(len(reference_points)))


def experimental_setup(total_runs=10, max_iterations=100, n_points=10000, taken_number=100) -> ExperimentResults:
    problems = {
        "dtlz5_5": partial(get_dtlz, filename="dtlz5_5"),
        "dtlz5_3": partial(get_dtlz, filename="dtlz5_3"),
        "dtlz7": partial(get_dtlz, filename="dtlz7"),
        "dtlz5_4": partial(get_dtlz, filename="dtlz5_4"),
        "forest_3": partial(get_forest_problem, n_objs=3),
        "forest_4": partial(get_forest_problem, n_objs=4),
        "RE31": partial(get_re, filename="RE31"),
        "RE32": partial(get_re, filename="RE32"),
        "RE33": partial(get_re, filename="RE33"),
        "RE34": partial(get_re, filename="RE34"),
        "RE35": partial(get_re, filename="RE35"),
        "RE36": partial(get_re, filename="RE36"),
        "RE37": partial(get_re, filename="RE37"),
        "RE41": partial(get_re, filename="RE41"),
        "RE42": partial(get_re, filename="RE42"),
        "RE61": partial(get_re, filename="RE61"),
    }

    methods = {
        "DSS_scipy": DSS_scipy_one_liner,
        "random_selection": random_selection,
        "total_random": total_random,
    }

    all_experiments = []
    for name, problem in problems.items():
        for method_name, method in methods.items():
            for runId in range(total_runs):
                all_experiments.append((max_iterations, name, problem, method_name, method, runId, n_points))
    return all_experiments


def extracted_experiment(inputs):
    max_iterations, name, problem, method_name, method, runId, n_points = inputs
    data, ideal, nadir, n_objs = problem()
    spacing_ind = SpacingIndicator(pf=data, zero_to_one=True, ideal=ideal, nadir=nadir)
    _, reference_points = generate_points(n_points, n_objs)

    asf_func = ReferencePointASF(preferential_factors=1, utopian_point=ideal, nadir=nadir, rho=0)

    def ref_solver(reference_point):
        asf_vals = asf_func(data, reference_point)
        index = np.argmin(asf_vals)
        return data[index], asf_vals[index]

    bad_reference_checker = partial(angle_distance, threshold=2)  # 2 degrees

    start = process_time()
    tries = 5
    while tries > 0:
        try:
            results = run_one_exp(
                method,
                ref_solver,
                reference_points,
                bad_reference_checker,
                max_iterations=max_iterations,
                thickness=1e-6,
            )
            break
        except Exception:
            tries -= 1
    if tries == 0:

        print(f"Error in {name} {method_name} {runId},")
        return None
    end = process_time()
    runtime = end - start
    results = exp_results(
        results=results,
        data=data,
        name=name,
        method=method_name,
        runID=runId,
        runtime=runtime,
        spacing_ind=spacing_ind,
    )
    # write results to file
    results_json = results.model_dump_json()
    with open(f"../results/{name}_{method_name}_{runId}.json", "w") as f:
        f.write(results_json)
    

In [5]:
all_experiments = experimental_setup(total_runs=5, max_iterations=500)

In [6]:
results = []
with Pool(parallel_processes) as p:
    max_exp = len(all_experiments)
    with tqdm(total=max_exp) as pbar:
        for i, result in enumerate(p.imap_unordered(extracted_experiment, all_experiments)):
            pbar.update()
            results.append(result)

  0%|          | 0/240 [00:00<?, ?it/s]

In [ ]:
results = ExperimentResults(results=[result for results in results if results is not None])

In [ ]:
test = results.model_dump_json()

with open("results.json", "w") as f:
    f.write(test)

In [5]:
data, ideal, nadir, n_objs = get_dtlz("dtlz5_3")

In [6]:
# Generate reference points

n_points = 10000


ref_points_flat, ref_points = generate_points(n_points, n_objs)
asf_func = ReferencePointASF(preferential_factors=1, utopian_point=ideal, nadir=nadir, rho=0)


def ref_solver(reference_point):
    asf_vals = asf_func(data, reference_point)
    index = np.argmin(asf_vals)
    return data[index], asf_vals[index]


bad_reference_checker = partial(angle_distance, threshold=2)  # 2 degrees

# How many bad reference points
bad = []
for ref in ref_points:
    bad.append(bad_reference_checker(reference_point=ref, solution=ref_solver(ref)[0]))

print("Fraction of bad reference points")
print(sum(bad) / len(bad))

Fraction of bad reference points
0.9644


In [7]:
results = run_one_exp(
    DSS_scipy_one_liner,
    ref_solver,
    ref_points,
    bad_reference_checker,
    max_iterations=500,
    thickness=1e-10,
)

Thickness is too small, breaking


In [9]:
solns = []
refs = []
bad_frac = []
success = []

for result in results:
    solns.append(result["solution"])
    refs.append(result["ref_point"])
    bad_frac.append(result["bad_fraction"])
    success.append(result["success"])


solns = pd.DataFrame(solns, columns=["f1", "f2", "f3"])
refs = pd.DataFrame(refs, columns=["f1", "f2", "f3"])

In [10]:
fig = ex.scatter_3d(solns, x="f1", y="f2", z="f3")

fig.add_scatter3d(
    x=data[:, 0],
    y=data[:, 1],
    z=data[:, 2],
    mode="markers",
    marker=dict(size=2),
)

# Color using success
fig.add_scatter3d(
    x=refs["f1"],
    y=refs["f2"],
    z=refs["f3"],
    mode="markers",
    marker=dict(size=5, color=["green" if s else "red" for s in success]),
)

# make projection orthogonal
fig.layout.scene.camera.projection.type = "orthographic"
fig.show()

In [ ]:
bad_hulls = []

for i in range(1, bad_refs.max() + 1):
    if i not in bad_refs:
        continue
    try:
        bad_hulls.append(ConvexHull(rotate_in(ref_points[bad_refs == i])))
    except:
        continue


bad_hulls_ = [rotate_out(hull.points[hull.vertices]) for hull in bad_hulls]

In [ ]:
# Plot the data and reference points

fig = ex.scatter_3d(
    x=[ideal[0]],
    y=[ideal[1]],
    z=[ideal[2]],
    width=800,
    height=700,
)

fig.add_scatter3d(
    x=data[:, 0],
    y=data[:, 1],
    z=data[:, 2],
    mode="markers",
    name="Solutions",
    opacity=0.7,
    marker=dict(size=7, color="#b2df8a"),
)

# found solutions#7570b3

fig.add_scatter3d(
    x=found_sols[:, 0],
    y=found_sols[:, 1],
    z=found_sols[:, 2],
    mode="markers",
    name="Found solutions",
    opacity=0.7,
    marker=dict(size=7, color="#1f78b4"),
)

fig.update(layout_coloraxis_showscale=False)

# Add reference points, show evaluated and bad reference points as green and black respectively and add legend

"""fig.add_scatter3d(
    x=ref_points[evaluated_refs != 0, 0],
    y=ref_points[evaluated_refs != 0, 1],
    z=ref_points[evaluated_refs != 0, 2],
    mode="markers",
    name="Evaluated reference points",
    opacity=0.8,
    marker=dict(size=7, color="green"),
)

fig.add_scatter3d(
    x=ref_points[:, 0],
    y=ref_points[:, 1],
    z=ref_points[:, 2],
    mode="markers",
    name="Reference points",
    opacity=0.1,
    marker=dict(size=2, color="black"),
)"""

"""for hull in bad_hulls_:
    fig.add_trace(
        go.Mesh3d(
            x=hull[:, 0],
            y=hull[:, 1],
            z=hull[:, 2],
            opacity=0.5,
            color="red",
            alphahull=0,
        )
    )"""

# Add ideal and nadir points

fig.add_trace(go.Scatter3d(x=[ideal[0]], y=[ideal[1]], z=[ideal[2]], mode="markers", name="Ideal"))

fig.add_trace(go.Scatter3d(x=[nadir[0]], y=[nadir[1]], z=[nadir[2]], mode="markers", name="Nadir"))


fig.layout.scene.camera.projection.type = "orthographic"

fig

In [ ]:
hv = []

for i in range(len(found_sols)):
    hv.append(wfg(found_sols[: i + 1], nadir.astype(float)))

hv = np.array(hv) / wfg(np.ascontiguousarray(data), nadir.astype(float))

ex.line(hv)

In [ ]:
max_iterations = 100
ex.line(np.cumsum([sum(bad_refs == i) if i in bad_refs else 0 for i in range(1, max_iterations + 1)]))

In [ ]:
bad_refs